# Trending Video Transformation Script

## Dynamic Daily Data Ingestion & CSV Joining ##


In [0]:
from datetime import datetime

# Make path dynamic to only transform the data from the current day's ingestion
date = '2025-04-01' #datetime.today().strftime('%Y-%m-%d')
path = f"abfss://raw_container_placeholder@datalake_placeholder.dfs.core.windows.net/{date}_Trending_Videos"

# Error Handeling for if today's data failed to be ingested and path doesn't exist
try:
    dbutils.fs.ls(path)
    # Only reading from the parent folder joins all the countries together into one large data frame
    df = spark.read.format("csv").option("header", True).option("inferSchema", True).load(path)
except Exception as e:
    #print(f"No Data for {date}, skipping ingestion. Terminating the Notebook")

    # Stop execution of the notebook
    dbutils.notebook.exit(f"ERROR: Missing Data {date} - Notebook Terminated")

## Data Transformations ##


##### Category Name Column - Leveraging Dictionary to Map Category ID with its respective name for Analysis #####
##### Country Name Column - Leveraging Dictionary to Map Country Code with its respective name for Analysis #####
##### Upload Date Column - Truncating Date Time Column to Just a Date Column #####
##### Video Engagment Statistic Columns - Video Metadata to Understand Engagement's Influence on Trending Status #####
##### Description Column - Limiting Character Output of Description Column to Resolve Synapse Analytics Errors #####
##### Video Duration Column - Updating Format of Video Duration to be in Minutes Format #####

In [0]:
from pyspark.sql.functions import udf, to_date, col, when, round, regexp_extract, coalesce, lit

# Category ID is a number, we need to map that number to the respective category for dashboard analytics
category_dict = {
    1: "Film & Animation",
    2: "Autos & Vehicles",
    10: "Music",
    15: "Pets & Animals",
    17: "Sports",
    18: "Short Movies",
    19: "Travel & Events",
    20: "Gaming",
    21: "Videoblogging",
    22: "People & Blogs",
    23: "Comedy",
    24: "Entertainment",
    25: "News & Politics",
    26: "Howto & Style",
    27: "Education",
    28: "Science & Technology",
    29: "Nonprofits & Activism",
    30: "Movies",
    31: "Anime/Animation",
    32: "Action/Adventure",
    33: "Classics",
    34: "Comedy",
    35: "Documentary",
    36: "Drama",
    37: "Family",
    38: "Foreign",
    39: "Horror",
    40: "Sci-Fi/Fantasy",
    41: "Thriller",
    42: "Shorts",
    43: "Shows",
    44: "Trailers"
}

# Country Code is an Abbreviation, we need to map that code to Full Country Name
countries_dict = {
    "IN": "India",
    "US": "United States",
    "BR": "Brazil",
    "ID": "Indonesia",
    "MX": "Mexico",
    "JP": "Japan",
    "DE": "Germany",
    "GB": "United Kingdom",
    "FR": "France",
    "KR": "South Korea"
}

# Method to handle the category mapping and country mapping creating udfs to use Python logic with PySpark
def map_category(category_id):
    return category_dict.get(category_id, "N/A")
map_category_udf = udf(map_category)

def map_country(country_code):
    return countries_dict.get(country_code, "N/A")
map_country_udf = udf(map_country)

# Cleaning / Adding columns to the dataframe
df_transformed = df.withColumn("CATEGORY_NAME", map_category_udf(col("CATEGORY_ID"))) \
                   .withColumn("UPLOAD_DATE", to_date(col("PUBLISHED_AT"), "yyyy-MM-dd")) \
                   .withColumn("DESCRIPTION", col("DESCRIPTION").substr(1, 2000)) \
                   .withColumn("COUNTRY_NAME", map_country_udf(col("COUNTRY_CODE"))) \
                   .withColumn("LIKE_TO_VIEW_RATIO", round((col("LIKE_COUNT") / col("VIEW_COUNT") * 100), 2)) \
                   .withColumn("COMMENT_TO_VIEW_RATIO", round((col("COMMENT_COUNT") / col("VIEW_COUNT") * 100), 2)) \
                   .withColumn("LIKE_TO_COMMENT_RATIO", when(col("COMMENT_COUNT") > 0, round((col("LIKE_COUNT") / col("COMMENT_COUNT")), 2)).otherwise(0)) \
                   .withColumn("VIDEO_DURATION_IN_MINUTES", round(
                        (coalesce(regexp_extract(col("DURATION"), r"(\d+)H", 1).cast("int"), lit(0)) * 60) + 
                        (coalesce(regexp_extract(col("DURATION"), r"(\d+)M", 1).cast("int"), lit(0))) + 
                        (coalesce(regexp_extract(col("DURATION"), r"(\d+)S", 1).cast("int"), lit(0)) / 60.0)
                   , 2))

# Replace null values (if any) with 0 for hours, minutes, or seconds
df_transformed = df_transformed.fillna({"VIDEO_DURATION_IN_MINUTES": 0})

# Drop the original TIME_DURATION column
df_transformed = df_transformed.drop("DURATION")                   

df_transformed.display()                   

VIDEO_ID TITLE CHANNEL_TITLE CHANNEL_ID PUBLISHED_AT DESCRIPTION TAGS CATEGORY_ID VIEW_COUNT LIKE_COUNT COMMENT_COUNT TRENDING_DATE TRENDING_DATE_RANK COUNTRY_CODE CATEGORY_NAME UPLOAD_DATE COUNTRY_NAME LIKE_TO_VIEW_RATIO COMMENT_TO_VIEW_RATIO LIKE_TO_COMMENT_RATIO VIDEO_DURATION_IN_MINUTES RkPj6AnKm0Y NiziU(니쥬) LOVE LINE (운명선) M/V JYP Entertainment UCaO6TYtlC8U5ttz62hTrZgg 2025-03-31T09:00:02Z NiziU(니쥬) LOVE LINE (운명선) M/V 2025.03.31 MON 6PM (KST) Release 📌Listen to LOVE LINE https://niziu.lnk.to/LOVELINE NiziU Official Homepage: https://niziu.com/ NiziU Official YouTube: https://www.youtube.com/@NiziUOfficial NiziU Official Facebook: https://www.facebook.com/NiziUinfoofficial/ NiziU Official Twitter: https://twitter.com/NiziU__official NiziU Official Instagram: https://www.instagram.com/niziu_info_official/ NiziU Official Artist Instagram: https://www.instagram.com/niziu_artist_official/ NiziU Official TikTok: https://www.tiktok.com/@niziu_official NiziU Official FANCLUB “WithU”: https://fc.niziu.com NiziU Official FANCLUB “WithU MOBILE”: https://m.niziu.com #NiziU #니쥬 #LOVELINE #NiziU_LOVELINE #NiziU_Korea_Comeback #니쥬한국컴백 Copyrights 2025 ⓒ JYP Entertainment. All Rights Reserved. JYP Entertainment | JYP | Make you happy | Step and a step | Sony | JYP nation | MV | M/V | 니쥬 | needyou | ニジュー | NiziU | 마야 | 마코 | 리마 | 리오 | 미이히 | 마유카 | 아야카 | 니나 | 리쿠 | maya | mako | rima | miihi | mayuka | rio | ayaka | nina | riku | アイドル | マヤ | マコ | リマ | リオ | ミイヒ | マユカ | アヤか | ニナ | リク | JYPさん | girl group | k-pop | j-pop | Press Play | NiziU Press Play | NiziU Korea Debut | NiziU Single Album | 1st Korea Single Album | 니쥬 한국 데뷔 | NiziU Comeback | HEARTRIS | 니쥬 러브라인 | NiziU LOVE LINE | 니쥬 한국 | 니쥬 한국컴백 | NiziU 러브라인 | NiziU Korea Comeback | 니쥬 트레일러 | 니쥬 티저 | NiziU Trailer 10 2732387 68977 14432 2025-04-01 1 JP Music 2025-03-31 Japan 2.52 0.53 4.78 3.45 JbPHJKQtWbI BE:FIRST / Blissful -from D.U.N.K. Showcase in K-Arena Yokohama- BE:FIRST Official UCi_AquB9uaI3-9xXkuWG7IQ 2025-03-31T13:00:31Z BE:FIRST 2025/5/28（水）発売ニューシングル「GRIT」LIVE盤に D.U.N.K. Showcase in K-Arena Yokohama「Blissful」含む BE:FIRSTのLIVEの模様を収録！ ▼BE:FIRST 7th Single “GRIT” 2025.5.28 On Sale https://befirst.tokyo/news/grit/ https://befirst.lnk.to/GRIT ▼BE:FIRST / Blissful - Music Video - https://www.youtube.com/watch?v=ZMcNU2hfD_M ▼BE:FIRST 2nd Album “2:BE” https://befirst-sp.com/2BE/ Now On Sale https://befirst.lnk.to/2BE ▼Streaming & Download https://BEFIRST.lnk.to/2_BE ▼BE:FIRST World Tour - Who is BE:FIRST? - https://befirst.tokyo/tour/worldtour2025/ ▼BE:FIRST / Music Video - Playlist - https://www.youtube.com/playlist?list=PLbnrvWONK6FdEWKeXArhrUMu53Xb7ruxl ▼BE:FIRST / Streaming https://befirst.lnk.to/Streaming ＜BE:FIRST PROFILE＞ SKY-HI率いるBMSGに所属する、SOTA、SHUNTO、MANATO、RYUHEI、JUNON、RYOKI、LEOの7人組ダンス＆ボーカルグループ。それぞれが歌・ダンス・ラップに対して高いクオリティとポテンシャルを持っているのと同時に、作詞・作曲・コレオグラフにまで発揮される音楽的感度の高さ、そして七者七様の個性を持った華やかさが魅力。「BE:FIRST」と名付けられたこの7人組は、プレデビューから日本の各種チャートの1位を席巻。ここからアジア、そして世界へと向けて偉大なる最初の一歩目を踏み出す。2024年12月から4都市9公演を回る自身初のドームツアー「BE:FIRST DOME TOUR 2024-2025 2:BE 」を開催。さらに2025年4月からアメリカ・アジア・ヨーロッパの全15都市を回る自身初となるワールドツアー『BE:FIRST World Tour - Who is BE:FIRST? -』の開催が決定。 ＜BE:FIRST SNS＞ Official Website：https://befirst.tokyo/ X : https://twitter.com/BEFIRSTofficial X (global): https://twitter.com/BEFIRST_global Instagram : https://www.instagram.com/befirst__official/ Facebook : https://www.facebook.com/BEFIRSTofficial TikTok : https://www.tiktok.com/@befirst_official YouTube Channel : https://www.youtube.com/c/BEFIRSTOfficial LINE : https://page.line.me/befirst ＜BMSG SNS＞ Official Website：https://bmsg.tokyo/ X：https://twitter.com/BMSG_official Instagram : https://www.instagram.com/bmsg_official/ YouTube Channel：https://www.youtube.com/c/BMSG_official #BEFIRST #BF_Blissful #D_U_N_K_ #BMSG #BME #BESTY #BEFIRSTXBESTY SKY-HI | スカイハイ | すかいはい | 日高 | ヒダカ | ひだか | 日高光啓 | AAA | トリプルエー | すっきり | ｽｯｷﾘ | sukkkiri | THEFIRST | ザファースト | ｻﾞﾌｧｰｽﾄ | ざふぁーすと | BMSG | ビーエムエスジー | ﾋﾞｰｴﾑｴｽｼﾞｰ | びーえむえすじー | ボーイズグループオーディション | ざすと | ザスト | ｻﾞｽﾄ |

## Pushing Transformed data to Transformed Layer ##

#### Creating Transformed File For Today's Ingested Data ####


In [0]:
# Merge Partioned Files Into a Single CSV and Clean Up Metadata 
df_transformed.coalesce(1).write.format('csv').mode('overwrite').option("header", True).option("path", f"abfss://transformed_container_placeholder@datalake_placeholder.dfs.core.windows.net/{date}_Trending_Videos").save()


# Find all files that aren't the csv and remove for clean up
files = dbutils.fs.ls(f"abfss://transformed_container_placeholder@datalake_placeholder.dfs.core.windows.net/{date}_Trending_Videos")

# Identify the actual CSV file so we can rename with a more clear description
csv_file = [f.path for f in files if f.name.startswith("part-") and f.name.endswith(".csv")][0]
new_csv_path = f"abfss://transformed_container_placeholder@datalake_placeholder.dfs.core.windows.net/{date}_Trending_Videos/{date}_Trending_Videos.csv"
dbutils.fs.mv(csv_file, new_csv_path)

# Remove all metadata files create by spark and keep only renamed csv file
for f in files:
    if not f.name.endswith(".csv"): 
        dbutils.fs.rm(f.path)


#### Adding Transformed Data to Historical Dataset ####


In [0]:
# Define Historical Dataset Path and create if it doesn’t exist
historical_path = "abfss://transformed_container_placeholder@datalake_placeholder.dfs.core.windows.net/Historical_Data/Historical_Trending_Videos.csv"

try:
    df_historical = spark.read.format("csv").option("header", True).load(historical_path)
except Exception as e:
    df_historical = None  # Set to None if it doesn’t exist


# Load today's data from the previous clean up task
today_path = f"abfss://transformed_container_placeholder@datalake_placeholder.dfs.core.windows.net/{date}_Trending_Videos/{date}_Trending_Videos.csv"
df_today = spark.read.format("csv").option("header", True).load(today_path)

# Append Historical and Today's dataframe together 
if df_historical is not None:
    df_historical = df_historical.unionByName(df_today)
else:
    df_historical = df_today

# Overwrite previous Historical Dataset with New Dataset Containing Today's Data
df_historical.coalesce(1).write.format("csv").mode("overwrite").option("header", True).option("path", "abfss://transformed_container_placeholder@datalake_placeholder.dfs.core.windows.net/Historical_Data").save()

#Perform Same Clean Up to Remove Metadata Files from Storage
files = dbutils.fs.ls(f"abfss://transformed_container_placeholder@datalake_placeholder.dfs.core.windows.net/Historical_Data")

# Identify the actual CSV file so we can rename with a more clear description
csv_file = [f.path for f in files if f.name.startswith("part-") and f.name.endswith(".csv")][0]
new_csv_path = f"abfss://transformed_container_placeholder@datalake_placeholder.dfs.core.windows.net/Historical_Data/Historical_Trending_Videos.csv"
dbutils.fs.mv(csv_file, new_csv_path)

# Remove all metadata files create by spark and keep only renamed csv file
for f in files:
    if not f.name.endswith(".csv"): 
        dbutils.fs.rm(f.path)
